# Geemap y GEE


Empezamos importando las librerías ee y geemap. No hace falta instalarlas porque ya vienen por defecto en el entorno de Google Colab.
La primera vez es neecsario hacer el Authenticate. Y dentro de Initialize debemos poner nuestro proyecto de Google Cloud

In [2]:
import ee
import geemap

ee.Authenticate()
ee.Initialize(project='ee-digdgeografo')

In [ ]:
Map = geemap.Map()
Map

Map(center=[0, 0], controls=(WidgetControl(options=['position', 'transparent_bg'], widget=SearchDataGUI(childr…

### Empezamos haciendo algo similar a lo que hemos visto en Javascript

In [ ]:
andalucia = ee.FeatureCollection('users/digdgeografo/curso_GEE/Andalucia')
Map.addLayer(andalucia, {}, "Andalucia")

In [ ]:
# Seleccionamos municipios
almonte = andalucia.filter(ee.Filter.eq('nombre', 'Almonte'))
Map.addLayer(almonte, {'color': 'red'}, "Almonte")

In [ ]:
# Seleccionamos por provincia
lobueno = andalucia.filter(ee.Filter.inList('provincia', ["Cádiz", "Huelva"]))
Map.addLayer(lobueno, {'color': 'blue'}, "Lobueno")

## Podemos trabajar con geometrías en el mapa tal y como hacíamos en el code editor
**Ahora vamos a dibujar** un rectangulo en el mapa para seleccionar los municipios que intersecten con nuestra geometría

In [ ]:
# Los rois tienen propiedades tal y como veíamos, entre ellas la geometría
# Como vemos se trata, ni más ni menos, que de un diccionario
Map.user_roi.getInfo()

{'geodesic': False,
 'type': 'Polygon',
 'coordinates': [[[-3.878174, 36.989391],
   [-3.878174, 37.287165],
   [-3.400269, 37.287165],
   [-3.400269, 36.989391],
   [-3.878174, 36.989391]]]}

In [ ]:
# Y dado que es un diccionario podemos trabajar con el objeto roi exactamente igual que haríamos con cualquier diccionario
print(Map.user_roi['coordinates'])
Map.user_roi_coords()

[[[-3.878174, 36.989391], [-3.878174, 37.287165], [-3.400269, 37.287165], [-3.400269, 36.989391], [-3.878174, 36.989391]]]


[-3.8782, 36.9894, -3.4003, 37.2872]

### Selección espacial con rois

In [ ]:
roi = Map.user_roi
selection = andalucia.filterBounds(roi)
Map.addLayer(selection, {'color': 'yellow'}, 'Geom Selection')

## Podemos abrir tantos mapas como queramos, creándolos como variables nuevas o sobreescribiendo la existente. Vamos a ver las opciones del mapa, que son muchas y muy intersantes

In [ ]:
Map2 = geemap.Map(center=(-6.2, 37.1), zoom=8, width= 2000, height=1000)
Map2

Map(center=[-6.2, 37.1], controls=(WidgetControl(options=['position', 'transparent_bg'], widget=SearchDataGUI(…

In [ ]:
dataset = ee.Image('CGIAR/SRTM90_V4')
elevation = dataset.select('elevation')
slope = ee.Terrain.slope(elevation)
Map2.setCenter(-6.2, 36.8, 10)
Map2.addLayer(slope, {"min": 0, "max": 60}, 'slope')

In [ ]:
# Diccionario de visualización
vis_params = {
  'min': 0,
  'max': 4000,
  'palette': ['006633', 'E5FFCC', '662A00', 'D8D8D8', 'F5F5F5']}
Map2.addLayer(elevation, vis_params, "DEM Vis")

## Volvemos con las Landsat!

In [ ]:
Map3 = geemap.Map()
Map3

Map(center=[0, 0], controls=(WidgetControl(options=['position', 'transparent_bg'], widget=SearchDataGUI(childr…

In [ ]:
vis_params = {'bands': ['SR_B5', 'SR_B4', 'SR_B3'], 'min': 0.0, 'max': 3000, 'opacity': 1.0, 'gamma': 1.2}
image = ee.Image('LANDSAT/LC08/C02/T1_L2/LC08_202034_20240722')
props = geemap.image_props(image)
print(props.getInfo()) # Otra vez un diccionario. Vamos a imprimirlo bien!
#Map.addLayer(image, vis_params, "Landsat Vis")

In [ ]:
bands = image.select(['SR_B7', 'SR_B5', 'SR_B2']) # Estamos generando una imagen solo con 3 bandas
Map3.addLayer(bands, {'min': 4000, 'max': 22000}, 'Pseudo True Color')

In [ ]:
new_image = image.select(['SR_B4', 'SR_B3', 'SR_B2'], ['Red', 'Green', 'Blue']) # Otra imagen con 3 bandas, en este caso también las renombramos
#band_names = new_image.bandNames()
Map3.addLayer(new_image, {'min': 4000, 'max': 22000}, 'True Color')

## Vamos con los índices!
### Pero primero hay que hacer algo reflectivo 🤔

In [ ]:
# NDWI image
ndwi = image_sr.normalizedDifference(['SR_B3', 'SR_B5'])
ndwiViz = {'min': 0, 'max': 0.8, 'palette': ['FFFFFF', '0000FF']}
Map3.addLayer(ndwi, ndwiViz, 'NDWI')

# NDWI masked (< 0.1).
ndwiMasked = ndwi.updateMask(ndwi.gte(0.1))
Map3.addLayer(ndwiMasked, {}, 'NDWI masked')

In [ ]:
### Ejercicio!
# Calculamos el ndvi y lo reclasificamos en umbrales

## Mosaicado

In [ ]:
Map4 = geemap.Map()

# Crear máscara de agua (NDWI > umbral)
water_mask = ndwi.gt(0.1)
land_mask = water_mask.Not() # Invertimos la máscara

# Aplicar máscaras a las visualizaciones
imageRGB = (image_sr.visualize(**{'bands': ['SR_B5', 'SR_B4', 'SR_B3'], 'max': 0.5})
            .updateMask(land_mask))  # Solo mostrar en tierra

ndwiRGB = (ndwi.visualize(**{
              'min': 0.1,
              'max': 0.8,
              'palette': ['FFFFFF', '0000FF']
           })
           .updateMask(water_mask))  # Solo mostrar en agua

# Crear el mosaico
mosaic = ee.ImageCollection([imageRGB, ndwiRGB]).mosaic()

# Añadir al mapa
Map4.addLayer(mosaic, {}, 'RGB-tierra + NDWI-agua')
Map4.centerObject(image, 10)  # Centrar en la imagen
Map4

Map(center=[37.47281412987213, -6.259111226806191], controls=(WidgetControl(options=['position', 'transparent_…

### Alternativa rápida con blend
https://developers.google.com/earth-engine/apidocs/ee-image-blend?hl=es-419

In [ ]:
# Crear visualizaciones con máscaras
imageRGB_masked = image_sr.visualize(**{'bands': ['SR_B6', 'SR_B5', 'SR_B2'], 'max': 0.5}).updateMask(land_mask)
ndwiRGB_masked = ndwi.visualize(**{'min': 0.1, 'max': 0.8, 'palette': ['FFFFFF', '0000FF']}).updateMask(water_mask)

# Combinar directamente
combined = imageRGB_masked.blend(ndwiRGB_masked)

Map4.addLayer(combined, {}, 'Combinado')

## Colecciones

In [ ]:
collection = ee.ImageCollection('LANDSAT/LC09/C02/T1_L2')
print(collection.size().getInfo())

613056


In [ ]:
imagel9 = collection.first()
geemap.image_props(imagel9).getInfo()

In [ ]:
Map5 = geemap.Map()
Map5.addLayer(imagel9, {}, "First image")
Map5.centerObject(imagel9, 6)
Map5

Map(center=[78.11273443375549, -15.96144067196992], controls=(WidgetControl(options=['position', 'transparent_…

### Filtramos la coleccion

In [ ]:
filtercol = collection.filterDate('2024-01-01', '2024-12-31')
filtercol.size()

In [ ]:
# Filtrado espacial
roi = ee.Geometry.Point(-6.1488, 37.0589)
filtercol = filtercol.filterBounds(roi)
filtercol.size()

In [ ]:
# Filtrado completo usando image properties
collection = ee.ImageCollection('LANDSAT/LC09/C02/T1_L2') \
    .filterDate('2024-01-01', '2024-12-31') \
    .filterBounds(roi) \
    .filterMetadata('CLOUD_COVER', 'less_than', 10) \
    .sort("CLOUD_COVER")

In [ ]:
collection.size()

In [ ]:
collection.aggregate_array('CLOUD_COVER')

In [ ]:
collection.aggregate_array('system:id').getInfo()

['LANDSAT/LC09/C02/T1_L2/LC09_202034_20240714',
 'LANDSAT/LC09/C02/T1_L2/LC09_202034_20240409',
 'LANDSAT/LC09/C02/T1_L2/LC09_202034_20240815',
 'LANDSAT/LC09/C02/T1_L2/LC09_202034_20240120',
 'LANDSAT/LC09/C02/T1_L2/LC09_202034_20241221',
 'LANDSAT/LC09/C02/T1_L2/LC09_202034_20240527',
 'LANDSAT/LC09/C02/T1_L2/LC09_202034_20240221',
 'LANDSAT/LC09/C02/T1_L2/LC09_202034_20240916',
 'LANDSAT/LC09/C02/T1_L2/LC09_202034_20241205',
 'LANDSAT/LC09/C02/T1_L2/LC09_202034_20241119']

In [ ]:
# Ordenar primero en el servidor
collection_sorted = collection.sort('CLOUD_COVER')

# Obtener los datos ya ordenados
ids = collection_sorted.aggregate_array('system:id').getInfo()
clouds = collection_sorted.aggregate_array('CLOUD_COVER').getInfo()

# Imprimir
for img_id, cloud in zip(ids, clouds):
    print(f"{img_id} - {cloud:.2f}%)")

LANDSAT/LC09/C02/T1_L2/LC09_202034_20240714 - 0.00%)
LANDSAT/LC09/C02/T1_L2/LC09_202034_20240409 - 0.06%)
LANDSAT/LC09/C02/T1_L2/LC09_202034_20240815 - 0.06%)
LANDSAT/LC09/C02/T1_L2/LC09_202034_20240120 - 0.07%)
LANDSAT/LC09/C02/T1_L2/LC09_202034_20241221 - 0.08%)
LANDSAT/LC09/C02/T1_L2/LC09_202034_20240527 - 0.09%)
LANDSAT/LC09/C02/T1_L2/LC09_202034_20240221 - 0.11%)
LANDSAT/LC09/C02/T1_L2/LC09_202034_20240916 - 1.24%)
LANDSAT/LC09/C02/T1_L2/LC09_202034_20241205 - 4.51%)
LANDSAT/LC09/C02/T1_L2/LC09_202034_20241119 - 6.10%)


## Compute a median image

In [ ]:
# Compute a median image and display.

Map6 = geemap.Map()
median = collection.median()
Map6.setCenter(-6.15, 37, 10)
Map6.addLayer(median, {'bands': ['SR_B4',  'SR_B3',  'SR_B2'], 'max': 20000}, 'median')
Map6

Map(center=[37, -6.15], controls=(WidgetControl(options=['position', 'transparent_bg'], widget=SearchDataGUI(c…

At each location in the output image, in each band, the pixel value is the median of all unmasked pixels in the input imagery (the images in the collection). In the previous example, median() is a convenience method for the following call:

## Create an image composite

In [ ]:
peninsula = ee.FeatureCollection('projects/ee-digdgeografo/assets/peninsula_iberica')

In [ ]:
collectionIb = ee.ImageCollection('LANDSAT/LC09/C02/T1_L2') \
    .filterBounds(peninsula) \
    .filterDate('2024-01-01', '2024-12-31')

In [ ]:
collectionIb.size().getInfo()

996

In [ ]:
spain = peninsula.filter(ee.Filter.eq("ADM0_A3", "ESP"))
portugal = peninsula.filter(ee.Filter.eq("ADM0_A3", "PRT"))
#Map.addLayer(portugal, {}, "Portugal")

In [ ]:
image = collectionIb.median().clip(spain)
Map6.addLayer(image, {'bands': ['SR_B4',  'SR_B3',  'SR_B2'], 'min': 7500, 'max': 20000}, 'Landsat 2024')

In [ ]:
## Mosaico y Mapeado de funciones a una colección

## Mosaico y mapeado de funciones
### mosaic() - primera imagen válida (orden temporal)
mosaic = collection.mosaic()  # Píxel = primera imagen sin máscara

#### qualityMosaic() - imagen con mejor calidad
mosaic = collection.qualityMosaic('NDVI')  # Píxel = imagen con mayor NDVI

https://developers.google.com/earth-engine/apidocs/ee-imagecollection-qualitymosaic?hl=es-419

In [ ]:
def process_image(image):
    # Aplicar factores de escala a bandas ópticas
    optical = image.select('SR_B.').multiply(0.0000275).add(-0.2)

    # Enmascarar nubes (opcional pero recomendado)
    qa = image.select('QA_PIXEL')
    cloud_mask = qa.bitwiseAnd(1 << 3).eq(0).And(qa.bitwiseAnd(1 << 4).eq(0))
    optical_masked = optical.updateMask(cloud_mask)

    # Calcular NDVI
    ndvi = optical_masked.normalizedDifference(['SR_B5', 'SR_B4']).rename('NDVI')

    # Reemplazar las bandas originales por las escaladas
    return image.addBands(optical_masked, None, True).addBands(ndvi)

# Aplicar a la colección
collectionIb_processed = collectionIb.map(process_image)

# Crear mosaico de calidad
mosaic_ib = collectionIb_processed.qualityMosaic('NDVI')

# Visualizar con valores en reflectividad (0-1)
vis_params = {
    'bands': ['SR_B4', 'SR_B3', 'SR_B2'],
    'min': 0,
    'max': 0.7,
    'gamma': 1.4
}

Map6.addLayer(mosaic_ib, vis_params, 'Mosaico Península Ibérica')

## Elegir la mejor imagen por años

In [3]:
roi = ee.Geometry.Point(-5.99, 36.96)

def best_image(year):

    start_date = ee.Date.fromYMD(year, 1, 1)
    end_date = start_date.advance(1, 'year')

    image = ee.ImageCollection('LANDSAT/LC09/C02/T1_L2') \
        .filterBounds(roi) \
        .filterDate(start_date, end_date) \
        .sort("CLOUD_COVER") \
        .first()

    return image

In [9]:
start_year = 2021
end_year = 2025
years = ee.List.sequence(start_year, end_year)
year_list = years.getInfo()
print(year_list)

[2021, 2022, 2023, 2024, 2025]


In [10]:
images = years.map(best_image)

In [11]:
count = images.size().getInfo()
print(count)

5


In [12]:
ee.ImageCollection(images).aggregate_array("CLOUD_COVER").getInfo()

[0.25, 0.02, 0, 0, 0]

In [13]:
ee.ImageCollection(images).aggregate_array("system:id").getInfo()

['LANDSAT/LC09/C02/T1_L2/LC09_202034_20211213',
 'LANDSAT/LC09/C02/T1_L2/LC09_202034_20220607',
 'LANDSAT/LC09/C02/T1_L2/LC09_202034_20230712',
 'LANDSAT/LC09/C02/T1_L2/LC09_202034_20240714',
 'LANDSAT/LC09/C02/T1_L2/LC09_202034_20250903']

In [17]:
Map7 = geemap.Map()

vis_params = {
    'bands': ['SR_B4', 'SR_B3', 'SR_B2'],
    'min': 7000,
    'max': 20000,
    'gamma': 1.4
}

for index in range(0, count):
    image = ee.Image(images.get(index))
    layer_name = "Image " + str(year_list[index])
    print(layer_name)
    Map7.addLayer(image, vis_params, layer_name, False)

Map7

Image 2021
Image 2022
Image 2023
Image 2024
Image 2025


Map(center=[0, 0], controls=(WidgetControl(options=['position', 'transparent_bg'], widget=SearchDataGUI(childr…

## Exports

Export data to Google Drive

In [ ]:
geemap.ee_export_vector_to_drive(fc, description="loquesea", folder="export")

Exporting countries...


## Export an ee.Image

In [19]:
import os

out_dir = os.path.expanduser("~/Downloads")
filename = os.path.join(out_dir, 'landsat.tif')
os.path.split(filename)[0]

'/root/Downloads'

### Exporting all bands as one single image

In [ ]:
geemap.ee_export_image(image_clip, filename=filename, scale=90, region=roi, file_per_band=False)

### Exporting each band as one image

In [ ]:
geemap.ee_export_image(image_clip, filename=filename, scale=90, region=roi, file_per_band=True)

### Export an image to Google Drive

In [ ]:
geemap.ee_export_image_to_drive(image_clip, description='landsat', folder='export', region=roi, scale=30)

Exporting landsat ...


## Download an ee.ImageCollection

In [ ]:
geemap.ee_export_image_collection(collection, scale=5, out_dir=out_dir)

In [ ]:
geemap.ee_export_image_collection_to_drive(collection, folder='export', scale=10)

## Extract pixels as a Numpy array

In [ ]:
import numpy as np
import matplotlib.pyplot as plt

img = ee.Image('LANDSAT/LC08/C01/T1_SR/LC08_038029_20180810') \
  .select(['B4', 'B5', 'B6'])

aoi = ee.Geometry.Polygon(
  [[[-110.8, 44.7],
    [-110.8, 44.6],
    [-110.6, 44.6],
    [-110.6, 44.7]]], None, False)

rgb_img = geemap.ee_to_numpy(img, region=aoi)
print(rgb_img.shape)

(373, 531, 3)


## <font color = 'red'>**GEE Lesson 18. Computing zonal statistics with Google Earth Engine**</font>

https://tutorials.geemap.org/Analysis/zonal_statistics/

In [26]:
Map8 = geemap.Map()
Map8

Map(center=[0, 0], controls=(WidgetControl(options=['position', 'transparent_bg'], widget=SearchDataGUI(childr…

In [29]:
fc = ee.FeatureCollection('users/giswqs/public/countries')

# Add Earth Engine dataset
dem = ee.Image('USGS/SRTMGL1_003')

# Set visualization parameters.
dem_vis = {
  'min': 0,
  'max': 4000,
  'palette': ['006633', 'E5FFCC', '662A00', 'D8D8D8', 'F5F5F5']}

# Add Earth Engine DEM to map
Map8.addLayer(dem, dem_vis, 'SRTM DEM')

# Add Landsat data to map
landsat = ee.Image('LE7_TOA_5YEAR/1999_2003')

landsat_vis = {
    'bands': ['B4', 'B3', 'B2'],
    'gamma': 1.4
}
Map8.addLayer(landsat, landsat_vis, "Landsat", False)

Map8.addLayer(fc, {}, 'countries')

## Estadísticas zonales para una imagen

In [36]:
out_dir = os.path.expanduser('~/Downloads')
if not os.path.exists(out_dir):
    os.makedirs(out_dir)

In [31]:
out_dem_stats = os.path.join(out_dir, 'dem_stats.csv')

# Allowed output formats: csv, shp, json, kml, kmz
# Allowed statistics type: MEAN, MAXIMUM, MINIMUM, MEDIAN, STD, MIN_MAX, VARIANCE, SUM
geemap.zonal_statistics(dem, fc, out_dem_stats, statistics_type='MEAN', scale=1000)

Computing statistics ...
Generating URL ...
Please wait ...
Data downloaded to /root/Downloads/dem_stats.csv
